## Resumo Descritivo do Código
Cria um mapa interativo que integra dados geográficos dos bairros com indicadores socioeconômicos e pontos de descarte irregular.

- **Visualização**: Mapa coroplético com 16 variáveis alternáveis (área, população, renda, IDH, etc.)
- **Camadas**: Pontos de descarte divididos em coletados (azul) e estimados (vermelho)  
- **Interatividade**: Menu horizontal para trocar variáveis, tooltips com informações dos bairros
- **Classificação**: Categoriza depósitos irregulares em 4 níveis de intensidade

**Objetivo**: Permitir análise espacial da relação entre indicadores urbanos e ocorrência de descartes irregulares.

## Imports e configurações iniciais

In [1]:
import folium
from branca.colormap import LinearColormap
import numpy as np
import json
import os
import geopandas as gpd
import pandas as pd
from folium import plugins
# Importar configurações de features
from setup_notebook import setup_path
setup_path()
from src.feature_config import *
from src.loader_tmpts import load_template

###  Open data

In [11]:
# Leitura da geometria dos bairros
path = '/home/akel/PycharmProjects/Data_ambiental/data/process/'
gdf = gpd.read_file(path + 'shape_bairros.gpkg').rename(
    columns={'NM_BAIRRO': 'Bairro'})

# Pontos de descartes
gpd_p = gpd.read_file(path + 'Pontos_descartes_ML.gpkg')

# Leitura das Features 1
df = pd.read_csv(path + "tabela_total_com_DIEs.csv")
# Leitura das Features 2
df2 = pd.read_csv(path + "Bairros_Ncoleta.csv")

#--------------------------------------------------
# Features1 + features 2
df = df.merge(df2, on="Bairro", how="left")
gdf_merged = gdf.merge(df, on="Bairro", how="left")

# Função de categorização
def categorizar_dies(dies):
    if dies == 0:
        return 1
    elif 1 <= dies <= 3:
        return 2
    elif 4 <= dies <= 6:
        return 3
    else:  # dies >= 7
        return 4

# Aplicar categorização
gdf_merged['Dies_cat'] = gdf_merged['DIEs'].apply(categorizar_dies)

# Criar cópias para uso
gdf1 = gdf_merged[['Bairro', 'geometry', 'Hab', 'IDH']]
gdf_m = gdf_merged.copy()

print("Dados processados e merge realizado.")




# leitura dos pontos de descartes
filename2="Pontos_descartes_ML.gpkg"
path='/home/akel/PycharmProjects/Data_ambiental/data/process/'
arquivo2 = os.path.join(path, filename2)
gpd_p = gpd.read_file(arquivo2)

Dados processados e merge realizado.


In [13]:
# Coordenadas do centro
centro_lat, centro_lon = -1.427897, -48.4162631

# Criar mapa base
m = folium.Map(
    location=[centro_lat, centro_lon],
    tiles="CartoDB Positron",
    zoom_start=13,
    control_scale=True
)

print("Mapa base criado.")

# Definir features para mapear
features_to_map = [
    'area_km2', 'Hab', 'Mor', 'Mor/Hab', 'N_ren', 'ren_avg', 'ren_mdn',
    'T.A.', 'IDH-R', 'IDH-L', 'IDH-E', 'IDH', 'PPR', 'DIEs', 'Dies_cat',
    'nd_med'
]

print(f"Total de features disponíveis para mapeamento: {len(features_to_map)}")
print("Features:", features_to_map)

# Configurar features
features_config = get_feature_config(
    gdf_m, features_to_map, color_palettes, feature_names, feature_palettes
)

print(f"Features configuradas com sucesso: {len(features_config)}")

# Configurar tooltips
tooltip_fields = ['Bairro'] + list(features_config.keys())
tooltip_aliases = ['Bairro: '] + [
    features_config[f]['name'] + ': ' for f in features_config.keys()
]

# Criar camadas para cada feature
for feature, config in features_config.items():
    layer = folium.FeatureGroup(name=config['name'], show=config['show'])

    folium.GeoJson(
        gdf_m,
        style_function=lambda x, feat=feature, cmap=config['colormap']: {
            'fillColor': (
                cmap(x['properties'][feat])
                if x['properties'][feat] is not None
                else "#808080"
            ),
            'color': 'black',
            'weight': 1,
            'fillOpacity': 0.6
        },
        tooltip=folium.GeoJsonTooltip(
            fields=tooltip_fields,
            aliases=tooltip_aliases,
            localize=True,
            style=(
                "background-color: white; border: 1px solid black; "
                "padding: 8px; max-width: 300px;"
            )
        )
    ).add_to(layer)

    layer.add_to(m)

# -----------------------------------------------------
# CAMADA 3 — PONTOS (Estimados / Dados)
# -----------------------------------------------------
ponto_colors = {
    "Estimados": "red",
    "Dados": "darkblue"}
layer_pontos = folium.FeatureGroup(name="Pontos (Estimados/Dados)", show=False)

for _, row in gpd_p.iterrows():
    bairro = row["Bairro"]
    lat = row["lat"]
    lon = row["lon"]
    cor = row["Cor"]  # Estimados ou Dados
    
    marker_color = ponto_colors.get(cor, "black")  # fallback
    
    popup_html = f"""
    <b>Bairro:</b> {bairro}<br>
    <b>Tipo:</b> {cor}<br>
    <b>Lat:</b> {lat:.5f}<br>
    <b>Lon:</b> {lon:.5f}
    """

    folium.CircleMarker(
        location=[lat, lon],
        radius=2,
        color=marker_color,
        fill=True,
        fill_color=marker_color,
        fill_opacity=0.9,
        popup=popup_html,
        tooltip=f"{bairro} — {cor}"
    ).add_to(layer_pontos)

layer_pontos.add_to(m)


print(f"{len(features_config)} camadas adicionadas ao mapa.")

# Add nome dos bairro no mapa.
rotulos_layer = folium.FeatureGroup(name="Nomes Bairros", show=True)

# Adiciona todos os rótulos de uma vez
for _, row in gdf_m.iterrows():
    centroid = row.geometry.centroid
    folium.Marker(
        location=[centroid.y, centroid.x],
        icon=folium.DivIcon(
            html=(
                '<div style="'
                'font-size: 10px; '
                'background-color: rgba(255, 255, 255, 0.3);'
                'text-align: center;'
                'padding: 2px 20 px;'
                'border-radius: 3px;'
                'white-space: nowrap;'
                'display: inline-block;'
                '">'
                f'{row["Bairro"]}'
                '</div>'
            )
        )
    ).add_to(rotulos_layer)

rotulos_layer.add_to(m)
print("Rótulos dos bairros adicionados.")


# 5. Preparar dados JavaScript
colormap_data_js = {}
for feature, config in features_config.items():
    clean_name = ''.join(
        c for c in config['name'] if c.isalnum() or c.isspace()
    )
    colormap_data_js[clean_name] = config['html']

# 6. Carregar e injetar JavaScript dinâmico
dynamic_js = load_template('dynamic_colormap.js')
# Substituir placeholder pelos dados
dynamic_js = dynamic_js.replace(
    '{{COLORMAP_DATA}}',
    json.dumps(colormap_data_js, ensure_ascii=False)
)
dynamic_js = dynamic_js.replace(
    '{{NAME_MAPPING}}',
    json.dumps(
        {
            config["name"]: name
            for name, config in zip(
                colormap_data_js.keys(), features_config.values()
            )
        },
        ensure_ascii=False
    )
)

m.get_root().html.add_child(folium.Element(dynamic_js))
print("JavaScript dinâmico configurado.")


# 7. Controle de camadas

# Após criar o mapa e todas as camadas
folium.LayerControl(collapsed=False).add_to(m)

change_legend = load_template('change_legend.js')
m.get_root().html.add_child(folium.Element(change_legend)) #js para não mesclar camadas

# 8. Carregar controle de legenda
legend_control = load_template('colormap_container.html')
m.get_root().html.add_child(folium.Element(legend_control))

# 9. Carregar JavaScript da legenda
legend_js = load_template('legend_control.js')
m.get_root().html.add_child(folium.Element(legend_js))

print("Controles e legendas adicionados.")

print(f"\n✅ Mapa criado com {len(features_config)} features temáticas!")
print("🎯 Controles:")
print(
    "   • Use o controle de camadas (canto superior direito) para "
    "alternar entre features"
)
print(
    "   • Use a lista de legendas (canto superior esquerdo) para "
    "seleção rápida"
)
print("   • Passe o mouse sobre os bairros para ver todos os dados")

# Salvar mapa
output_path = '/home/akel/PycharmProjects/Data_ambiental/docs/mapa_bairros_interativo_folium.html'
m.save(output_path)
print(f"\nMapa salvo em: {output_path}")

# Opcional: Exibir o mapa no notebook
display(m)

Mapa base criado.
Total de features disponíveis para mapeamento: 16
Features: ['area_km2', 'Hab', 'Mor', 'Mor/Hab', 'N_ren', 'ren_avg', 'ren_mdn', 'T.A.', 'IDH-R', 'IDH-L', 'IDH-E', 'IDH', 'PPR', 'DIEs', 'Dies_cat', 'nd_med']
Features configuradas com sucesso: 16
16 camadas adicionadas ao mapa.
Rótulos dos bairros adicionados.
JavaScript dinâmico configurado.
Controles e legendas adicionados.

✅ Mapa criado com 16 features temáticas!
🎯 Controles:
   • Use o controle de camadas (canto superior direito) para alternar entre features
   • Use a lista de legendas (canto superior esquerdo) para seleção rápida
   • Passe o mouse sobre os bairros para ver todos os dados

Mapa salvo em: /home/akel/PycharmProjects/Data_ambiental/docs/mapa_bairros_interativo_folium.html
